In [1]:
from pytorch_pretrained_bert.tokenization import BertTokenizer, WordpieceTokenizer
from pytorch_pretrained_bert.modeling import BertForPreTraining, BertConfig, BertForMaskedLM
from pathlib import Path
import torch
from fastai.text import Tokenizer, Vocab
import pandas as pd
import collections
import os
from tqdm import tqdm, trange
import sys
import random
import numpy as np
import apex
module_path = os.path.abspath(os.path.join('../../bert_fastai'))
if module_path not in sys.path:
    sys.path.append(module_path)

from bert_fastai import ExtensibleBertTokenizer
from bert_fastai import BERTDataset, InputFeatures, create_corpus
from torch.utils.data import DataLoader, RandomSampler
from torch.utils.data.distributed import DistributedSampler
from pytorch_pretrained_bert.optimization import BertAdam
import datetime

In [2]:
pd.set_option('display.max_colwidth', -1)
run_start_time = datetime.datetime.today().strftime('%Y-%m-%d_%H-%M-%S')

In [3]:
DATA_PATH = Path('../data/')

MODEL_PATH=Path('../models/')
LOG_PATH=Path('../logs/')
MODEL_PATH.mkdir(exist_ok=True)

model_state_dict = None

BERT_PRETRAINED_PATH = Path('../../bert_fastai/pretrained-weights/uncased_L-12_H-768_A-12/')
# BERT_PRETRAINED_PATH = Path('../../bert_fastai/pretrained-weights/cased_L-12_H-768_A-12/')
# BERT_PRETRAINED_PATH = Path('../../bert_fastai/pretrained-weights/uncased_L-24_H-1024_A-16/')

LOG_PATH.mkdir(exist_ok=True)

In [4]:
parameters = {
    "train_file": DATA_PATH/'intent_raw_lm.txt',
    "run_text": "Finetune language model",
    "data_dir": DATA_PATH,
    "task_name": "intent_classification_lm",
    "bert_model": BERT_PRETRAINED_PATH,
    "output_dir": MODEL_PATH/'output',
    "log_path": LOG_PATH,
    "max_seq_length": 512,
    "do_lower_case": True,
    "train_batch_size": 32,
    "eval_batch_size": 8,
    "learning_rate": 5e-5,
    "num_train_epochs": 3.0,
    "warmup_proportion": 0.1,
    "no_cuda": False,
    "local_rank": -1,
    "seed": 42,
    "gradient_accumulation_steps": 1,
    "optimize_on_cpu": False,
    "fp16": True,
    "loss_scale": 128,
    "on_memory": True
}

In [5]:
import logging

logfile = str(LOG_PATH/'log-{}-{}.txt'.format(run_start_time, parameters["run_text"]))

logging.basicConfig(
    level=logging.INFO,
    format='%(asctime)s - %(levelname)s - %(name)s -   %(message)s',
    datefmt='%m/%d/%Y %H:%M:%S',
    handlers=[
        logging.FileHandler(logfile),
        logging.StreamHandler(sys.stdout)
    ])

logger = logging.getLogger()

In [6]:
def get_texts():
    unlabelled = pd.read_csv('../../webchat/data/csv/processed_messages_v2.csv.gz', compression='gzip')

    return list(unlabelled['customer_two_messages'].values)


# intent_corpus = get_texts()
# imdb_corpus = list(np.concatenate([trn_texts,val_texts]))

In [8]:
# type(intent_corpus), len(intent_corpus)

In [9]:
main_tokenizer = BertTokenizer.from_pretrained(BERT_PRETRAINED_PATH/'vocab.txt', do_lower_case=parameters['do_lower_case'])

02/01/2019 00:37:15 - INFO - pytorch_pretrained_bert.tokenization -   loading vocabulary file ../../bert_fastai/pretrained-weights/uncased_L-12_H-768_A-12/vocab.txt from cache at ../../bert_fastai/pretrained-weights/uncased_L-12_H-768_A-12/vocab.txt


In [10]:
model = BertForPreTraining.from_pretrained(BERT_PRETRAINED_PATH)

02/01/2019 00:37:17 - INFO - pytorch_pretrained_bert.modeling -   loading archive file ../../bert_fastai/pretrained-weights/uncased_L-12_H-768_A-12 from cache at ../../bert_fastai/pretrained-weights/uncased_L-12_H-768_A-12
02/01/2019 00:37:17 - INFO - pytorch_pretrained_bert.modeling -   Model config {
  "attention_probs_dropout_prob": 0.1,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "max_position_embeddings": 512,
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "type_vocab_size": 2,
  "vocab_size": 30522
}



### Bert Finetuning

In [11]:
BERT_DATA_PATH = Path('../data/toxic_comments/')

In [13]:
# BERT_TRAINED_MODEL_PATH = Path('../trained_model/toxic_comments')
# (BERT_TRAINED_MODEL_PATH).mkdir(exist_ok=True)

In [15]:
n_gpu = torch.cuda.device_count()
n_gpu

4

In [16]:
parameters['train_batch_size'] = int(parameters['train_batch_size'] / parameters['gradient_accumulation_steps'])

In [17]:
random.seed(parameters['seed'])
np.random.seed(parameters['seed'])
torch.manual_seed(parameters['seed'])
if n_gpu > 0:
    torch.cuda.manual_seed_all(parameters['seed'])

In [18]:
# tokenizer = ExtensibleBertTokenizer.from_pretrained('../data/vocab_1.txt')
tokenizer = main_tokenizer

In [19]:
len(tokenizer.vocab)

30522

In [20]:
# create_corpus(intent_corpus, str(parameters['train_file']))

In [21]:
num_train_steps = None
print("Loading Train Dataset", parameters['train_file'])
train_dataset = BERTDataset(parameters['train_file'], tokenizer, seq_len=parameters['max_seq_length'],
                        corpus_lines=None, on_memory=parameters['on_memory'])
num_train_steps = int(
    len(train_dataset) / parameters['train_batch_size'] / parameters['gradient_accumulation_steps'] * parameters['num_train_epochs'])


Loading Dataset: 101533it [00:00, 484327.29it/s]

Loading Train Dataset ../data/intent_raw_lm.txt


Loading Dataset: 4897571it [00:07, 624801.85it/s]


In [22]:
import pdb
def get_sample(i):
#     pdb.set_trace()
    return train_dataset[i]

In [23]:
len(train_dataset)

2303519

In [24]:
# model = new_model
device = torch.device("cuda")

if parameters['fp16']:
    model.half()
    model.to(device)

In [25]:
if parameters['local_rank'] != -1:
    try:
        from apex.parallel import DistributedDataParallel as DDP
    except ImportError:
        raise ImportError("Please install apex from https://www.github.com/nvidia/apex to use distributed and fp16 training.")
    model = DDP(model)
elif n_gpu > 1:
    model = torch.nn.DataParallel(model)

In [26]:
def warmup_linear(x, warmup=0.002):
    if x < warmup:
        return x/warmup
    return 1.0 - x

In [27]:
# optimizer_grouped_parameters

In [28]:
# Prepare optimizer
param_optimizer = list(model.named_parameters())
no_decay = ['bias', 'LayerNorm.bias', 'LayerNorm.weight']
optimizer_grouped_parameters = [
    {'params': [p for n, p in param_optimizer if not any(nd in n for nd in no_decay)], 'weight_decay': 0.01},
    {'params': [p for n, p in param_optimizer if any(nd in n for nd in no_decay)], 'weight_decay': 0.0}
    ]
t_total = num_train_steps
if parameters['local_rank'] != -1:
    t_total = t_total // torch.distributed.get_world_size()
if parameters['fp16']:
    try:
        from apex.optimizers import FP16_Optimizer
        from apex.optimizers import FusedAdam
    except ImportError:
        raise ImportError("Please install apex from https://www.github.com/nvidia/apex to use distributed and fp16 training.")

    optimizer = FusedAdam(optimizer_grouped_parameters,
                          lr=parameters['learning_rate'],
                          bias_correction=False,
                          max_grad_norm=1.0)
    if parameters['loss_scale'] == 0:
        optimizer = FP16_Optimizer(optimizer, dynamic_loss_scale=True)
    else:
        optimizer = FP16_Optimizer(optimizer, static_loss_scale=parameters['loss_scale'])

else:
    optimizer = BertAdam(optimizer_grouped_parameters,
                         lr=parameters['learning_rate'],
                         warmup=parameters['warmup_proportion'],
                         t_total=t_total)

In [ ]:
global_step = 0

logger.info("***** Running training *****")
logger.info("  Num examples = %d", len(train_dataset))
logger.info("  Batch size = %d", parameters['train_batch_size'])
logger.info("  Num steps = %d", num_train_steps)

if parameters['local_rank'] == -1:
    train_sampler = RandomSampler(train_dataset)
else:
    #TODO: check if this works with current data generator from disk that relies on file.__next__
    # (it doesn't return item back by index)
    train_sampler = DistributedSampler(train_dataset)
train_dataloader = DataLoader(train_dataset, sampler=train_sampler, batch_size=parameters['train_batch_size'])

model.train()
for _ in trange(int(parameters['num_train_epochs']), desc="Epoch"):
    tr_loss = 0
    nb_tr_examples, nb_tr_steps = 0, 0
    for step, batch in enumerate(tqdm(train_dataloader, desc="Iteration")):
        batch = tuple(t.to(device) for t in batch.values())
        input_ids, input_mask, segment_ids, lm_label_ids, is_next = batch
        loss = model(input_ids, segment_ids, input_mask, lm_label_ids, is_next)
#         loss = model(input_ids, segment_ids, input_mask, lm_label_ids)
        if n_gpu > 1:
            loss = loss.mean() # mean() to average on multi-gpu.
        if parameters['gradient_accumulation_steps'] > 1:
            loss = loss / parameters['gradient_accumulation_steps']
        if parameters['fp16']:
            optimizer.backward(loss)
        else:
            loss.backward()
        tr_loss += loss.item()
        nb_tr_examples += input_ids.size(0)
        nb_tr_steps += 1
        if (step + 1) % parameters['gradient_accumulation_steps'] == 0:
            # modify learning rate with special warm up BERT uses
            lr_this_step = parameters['learning_rate'] * warmup_linear(global_step/num_train_steps, parameters['warmup_proportion'])
            for param_group in optimizer.param_groups:
                param_group['lr'] = lr_this_step
            optimizer.step()
            optimizer.zero_grad()
            global_step += 1

02/01/2019 00:38:23 - INFO - root -   ***** Running training *****
02/01/2019 00:38:23 - INFO - root -     Num examples = 2303519
02/01/2019 00:38:23 - INFO - root -     Batch size = 32
02/01/2019 00:38:23 - INFO - root -     Num steps = 215954
Iteration:   0%|          | 0/71985 [00:00<?, ?it/s]02/01/2019 00:38:23 - INFO - bert_fastai.bert_dataset -   *** Example ***
02/01/2019 00:38:23 - INFO - bert_fastai.bert_dataset -   guid: 0
02/01/2019 00:38:23 - INFO - bert_fastai.bert_dataset -   tokens: [CLS] [MASK] i need my annual boiler [MASK] . [SEP] [MASK] trying to [MASK] it says ‘ not due yet [MASK] [SEP]
02/01/2019 00:38:23 - INFO - bert_fastai.bert_dataset -   input_ids: 101 103 1045 2342 2026 3296 15635 103 1012 102 103 2667 2000 103 2009 2758 1520 2025 2349 2664 103 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

02/01/2019 00:38:23 - INFO - bert_fastai.bert_dataset -   segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

02/01/2019 00:38:23 - INFO - bert_fastai.bert_dataset -   Is next sentence label: 1 
02/01/2019 00:38:23 - INFO - bert_fastai.bert_dataset -   *** Example ***
02/01/2019 00:38:23 - INFO - bert_fastai.bert_dataset -   guid: 3
02/01/2019 00:38:23 - INFO - bert_fastai.bert_dataset -   tokens: [CLS] is there any [MASK] of contact ##ing [MASK] engineer , so that he doesn ' t have a wasted journey ? , [SEP] thank you [SEP]
02/01/2019 00:38:23 - INFO - bert_fastai.bert_dataset -   input_ids: 101 2003 2045 2151 103 1997 3967 2075 103 3992 1010 2061 2008 2002 2987 1005 1056 2031 1037 13842 4990 1029 1010 102 4067 2017 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

02/01/2019 00:38:23 - INFO - bert_fastai.bert_dataset -   segment_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

Iteration:   0%|          | 188/71985 [01:13<7:59:41,  2.49it/s]


...

Iteration:  23%|██▎       | 16663/71985 [1:28:52<4:45:04,  3.23it/s]


Iteration:  23%|██▎       | 16776/71985 [1:29:28<4:51:05,  3.16it/s]


Iteration:  23%|██▎       | 16889/71985 [1:30:04<4:53:08,  3.13it/s]


Iteration:  24%|██▎       | 17002/71985 [1:30:40<4:48:00,  3.18it/s]


Iteration:  24%|██▎       | 17010/71985 [1:30:43<4:47:54,  3.18it/s]

In [ ]:
logger.info("** ** * Saving fine - tuned model ** ** * ")
output_model_file = os.path.join(MODEL_PATH, "intent_language_model_{}.bin".format(run_start_time))
if n_gpu > 1:
    torch.save(model.module.state_dict(), output_model_file)
else:
    torch.save(model.state_dict(), output_model_file)